In [ ]:
import numpy as np
import pandas as pd

pd.options.plotting.backend = "plotly"

from gettsim import (
    compute_taxes_and_transfers,
    create_synthetic_data,
    set_up_policy_environment,
)

# Präsenzphase: Kindergeld und Kinderfreibetrag

Nachdem Sie sich in der Selbstlernphase etwas mit GETTSIM vertraut gemacht haben, werden wir es heute erneut nutzen, 
um die Mechanik von Kindergeld und Kinderfreibetrag besser zu verstehen.

Wir werden Ehepartner ohne Kinder, mit einem Kind und mit zwei Kindern vergleichen. Die Einkommen beider
Ehepartner sind identisch. 

## Datensatzerstellung (2 Minuten)

Unsere Daten benötigen dasselbe Format, das wir in der Selbstlernphase verwendet haben, mit einer Zeile
pro Haushaltsmitglied. Dafür verwendenden wir die `create_synthetic_data` Funktion, die wir schon in der Selbstlernphase verwendet haben.

In [ ]:
min_einkommen = 1500
max_einkommen = 8000
anzahl_schritte = 131

inputs_2e_0k = create_synthetic_data(
    n_adults=2,
    n_children=0,
    specs_heterogeneous={
        "bruttolohn_m": [
            [i, i] for i in np.linspace(min_einkommen, max_einkommen, anzahl_schritte)
        ],
    },
)
max_ids = {
    "p_id": inputs_2e_0k["p_id"].max(),
    "tu_id": inputs_2e_0k["tu_id"].max(),
    "hh_id": inputs_2e_0k["hh_id"].max(),
}

In [ ]:
inputs_2e_1k = create_synthetic_data(
    n_adults=2,
    n_children=1,
    specs_heterogeneous={
        "bruttolohn_m": [
            [i, i, 0]
            for i in np.linspace(min_einkommen, max_einkommen, anzahl_schritte)
        ],
    },
)
for this_id, max_id in max_ids.items():
    inputs_2e_1k[this_id] += 1 + max_id
max_ids = {
    "p_id": inputs_2e_1k["p_id"].max(),
    "tu_id": inputs_2e_1k["tu_id"].max(),
    "hh_id": inputs_2e_1k["hh_id"].max(),
}

inputs_2e_2k = create_synthetic_data(
    n_adults=2,
    n_children=2,
    specs_heterogeneous={
        "bruttolohn_m": [
            [i, i, 0, 0]
            for i in np.linspace(min_einkommen, max_einkommen, anzahl_schritte)
        ],
    },
)
for this_id, max_id in max_ids.items():
    inputs_2e_2k[this_id] += 1 + max_id

## Gruppieren der Datensätze (1 Minute)

Da alle Datensätze die gleiche Struktur haben, empfiehlt es sich, sie direkt aneinander zu hängen. Im Index können wir über den key "Anzahl der Kinder" identifiezieren aus welchem ursprünglichen Datensatz die Zeile stammt.

Die GETTSIM Funktion können wir dann im nächsten Schritt direkt auf alle Haushalte aufeinmal anwenden.

In [ ]:
inputs = pd.concat(
    [
        inputs_2e_0k,
        inputs_2e_1k,
        inputs_2e_2k,
    ],
    keys=["keine Kinder", "ein Kind", "zwei Kinder"],
    names=["Anzahl der Kinder", "lfd_nr"],
)
inputs

Man kann nun folgerndermaßen auf die einzelnen Gruppen zugreifen.

In [ ]:
inputs.loc["ein Kind"]

Außerdem setzen wir das zu versteuernde Einkommen auf das 12-fache des monatlichen Haushaltsbruttoeinkommens.

In [ ]:
inputs["_zu_verst_eink_ohne_kinderfreib_tu"] = (
    inputs.groupby("tu_id")["bruttolohn_m"].transform("sum") * 12
)

## Anwendung von GETTSIM für Kindergeld und Steuern (5 Minuten)

Zunächst setzen wir wieder wie in der Einführung das Steuersystem für 2023 auf.

In [ ]:
params_dict, policy_func_dict = set_up_policy_environment(2023)

Außerdem bestimmen wir wieder die Targets (Kindergeld, Einkommensteuer und Solidaritätszuschlag) sowie die Spalten, die überschrieben werden sollen.

In [ ]:
columns_overriding_functions = [
    "_zu_verst_eink_ohne_kinderfreib_tu",
]

targets = ["kindergeld_m_tu", "eink_st_tu", "soli_st_tu"]

Nun rufen wir GETTSIM auf.

Funktionen und Parameter übernehmen wir direkt aus dem Steuersystem: `policy_func_dict` und `params_dict`.

In [ ]:
ergebnisse = compute_taxes_and_transfers(
    data=inputs,
    functions=policy_func_dict,
    columns_overriding_functions=columns_overriding_functions,
    params=params_dict,
    targets=targets,
    rounding=True,
)

Hier sind die Ergebnisse. Die oberen Zeile gehören zu den Haushalten ohne Kinder, die unteren zu jenen mit zwei Kindern.

In [ ]:
ergebnisse

## Berechnung jährlicher Werte auf Steuersubjektsebene, schöne Variablennamen (5 Minuten)

Wie Sie an dem DataFrame oberhalb dieser Zelle sehen, sind die Werte für alle Mitglieder einer Steuereinheit repliziert. 

Außerdem ist das Kindergeld auf monatlicher Ebene, für die Vergleichbarkeit brauchen wir aber jährliche Werte.

Zunächst verknüpfen wir die Ergebnisse aus der GETTSIM-Funktion mit unserem `input` Datensatz. 

In [ ]:
gesamt = inputs.reset_index().join(ergebnisse).set_index(inputs.index.names)
gesamt = gesamt[
    [
        "p_id",
        "tu_id",
        "hh_id",
        "bruttolohn_m",
        "eink_st_tu",
        "kindergeld_m_tu",
        "soli_st_tu",
    ]
]
# Jährliches Kindergeld
gesamt["Kindergeld"] = gesamt["kindergeld_m_tu"] * 12
# Lösche monatliche Werte
gesamt = gesamt.drop(
    "kindergeld_m_tu",
    axis=1,
)
# Spaltennamen für späteres Plotten
gesamt = gesamt.rename(
    columns={
        "eink_st_tu": "Einkommensteuer",
        "soli_st_tu": "Soli",
    },
)
gesamt

## Berechnung der Gesamtbruttoeinkünfte von Steuersubjekten (2 Minuten)

Wir summieren nun die Einkünfte eines Haushalts auf (das funktioniert nur, weil wir alle anderen
Einkünfte neben dem monatlichen Bruttolohn auf Null und die Einkünfte der Kinder auf fehlend
gesetzt haben).

In [ ]:
gesamteink_tu = gesamt.groupby("tu_id")["bruttolohn_m"].sum() * 12
gesamteink_tu.name = "Gesamteinkünfte Steuersubjekt"
# Besser Integer, da wir es später als Index verwenden
gesamteink_tu = gesamteink_tu.astype(int)
gesamteink_tu

In [ ]:
final = gesamt.merge(right=gesamteink_tu, left_on="tu_id", right_index=True)
final

In [ ]:
# Behalte nur eine Zeile pro Steuersubjekt
final = (
    final.reset_index()
    .drop_duplicates("tu_id")
    .set_index(["Anzahl der Kinder", "Gesamteinkünfte Steuersubjekt"])
    .sort_index()
)
# Behalte nur relevante Spalten
final = final[["Einkommensteuer", "Soli", "Kindergeld"]]
final

## Berechnung des Steuervorteils aus der Einkommensteuer für Haushalte mit Kindern im Vergleich zu Haushalten ohne Kinder (2 Minuten)

In [ ]:
# Setze Steuervorteil auf Null, bleibt nur so, falls keine Kinder vorhanden
final["Einkommensteuervorteil"] = 0.0
# Rechne Steuervorteil aus. Unklar, warum `to_list()` notwendig ist -- ist aber kein
# Problem, solange alles korrekt sortiert ist.
for n_kinder in "ein Kind", "zwei Kinder":
    final.loc[n_kinder, "Einkommensteuervorteil"] = (
        final.loc["keine Kinder", "Einkommensteuer"]
        - final.loc[n_kinder, "Einkommensteuer"]
        - final.loc["keine Kinder", "Kindergeld"]
        + final.loc[n_kinder, "Kindergeld"]
    ).to_list()
final

## Plots Kindergeld, Einkommensteuer, Vorteil für Haushalte mit Kindern (3 Minuten)

In [ ]:
final.reset_index().plot.line(
    x="Gesamteinkünfte Steuersubjekt",
    y="Kindergeld",
    color="Anzahl der Kinder",
    title="Kindergeld nach Anzahl der Kinder",
)

In [ ]:
final.reset_index().plot.line(
    x="Gesamteinkünfte Steuersubjekt",
    y="Einkommensteuer",
    color="Anzahl der Kinder",
    title="Einkommensteuer nach Anzahl der Kinder",
)

In [ ]:
final.reset_index().plot.line(
    x="Gesamteinkünfte Steuersubjekt",
    y="Einkommensteuervorteil",
    color="Anzahl der Kinder",
    title="Steuervorteil nach Anzahl der Kinder",
)

## Aufgabe 1: Interpretation der Dualität Kindergeld / Kinderfreibetrag (15 Minuten)

Warum sind die Kurven für die Steuervorteile für Einkommen bis in den Bereich von ca. 90.000 Haushaltseinkommen flach?

Falls Sie Probleme bei der Interpretation haben, ist diese Übersicht der Lohnsteuerhilfe vermutlich nützlich für Sie: https://www.vlh.de/fileadmin/images/infografiken/fullsize/vlh_kindergeld_kinderfreibetrag.jpg

Warum sind die Kurven flach für sehr hohe Einkommen?

Warum steigen die Kurven im Bereich dazwischen nahezu linear an?

## Aufgabe 2: Gesamter Steuervorteil (10 Minuten).
*Überspringen, falls sonst weniger als 10 Minuten für Aufgabe 3.*

Wiederholen Sie die Berechnung des Steuervorteils von oben, beziehen Sie nun jedoch den Soli mit ein.

Erstellen Sie zwei Grafiken, wieder auf Ebene der Steuersubjekte: 

1. Solidaritätszuschlag nach Gesamteinkünften
2. Gesamter Steuervorteil nach Gesamteinkünften

Interpretieren Sie Ihre Ergebnisse (Sie dürfen gern Internetrecherche betreiben)!

## Aufgabe 3: Fairness (10 Minuten)

Inwiefern halten Sie es für gerechtfertigt / sinnvoll, das besserverdienende Familien höhere Steuerersparnisse haben? 

Falls ein gewisser Betrag verfassungsrechtlich zwangsläufig ist: Halten Sie die Höhe für gerechtfertigt? Auch hier dürfen Sie gern Internetrecherche betreiben!


*Hier Platz für Ihre Antwort*

## Aufgabe 4: Pentabilities (10 Minuten)

Bitte bewerten Sie die Beiträge zur Gruppenarbeit in der Pentabilities-App. Bitte
vergeben Sie über alle 5 Dimensionen hinweg Punkte für die Verhaltensweisen, welche Sie
heute beobachten konnten. Denken Sie bitte daran, sowohl die Beiträge der
Kommiliton:innen Ihrer Gruppe als auch Ihre eigenen zu bewerten.